In [1]:
from transformers import BertTokenizer, BertModel, AutoTokenizer, AutoModelForSeq2SeqLM

model_checkpoint="/home/remote/dev/llm/Helsinki-NLP/opus-mt-mul-en_train-base-model-en-to-pt-5k-training-length/checkpoint-20000"

# model_checkpoint="/home/remote/dev/llm/Helsinki-NLP/opus-mt-mul-en-word-fine-tune-en-to-pt-1k/checkpoint-3000-words-to-sentences-1k-epochs-5k-train/checkpoint-16485-backwards-pt-to-en-continue-finetune/checkpoint-43960"
# model_checkpoint='marian-finetuned-kde4-en-to-fr/checkpoint-2996'


model = AutoModelForSeq2SeqLM.from_pretrained(model_checkpoint,  output_hidden_states=True, output_attentions=True).to("cuda")

tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)

/home/remote/miniconda3/envs/kubi/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/remote/miniconda3/envs/kubi/lib/python3.10/site-packages/transformers/models/marian/tokenization_marian.py:175: UserWarning: Recommended: pip install sacremoses.
  warnings.warn("Recommended: pip install sacremoses.")


In [52]:
model_checkpoint1="Helsinki-NLP/opus-mt-en-mt"
en_tokenizer=AutoTokenizer.from_pretrained(model_checkpoint1)

/home/remote/miniconda3/envs/kubi/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/home/remote/miniconda3/envs/kubi/lib/python3.10/site-packages/transformers/models/marian/tokenization_marian.py:175: UserWarning: Recommended: pip install sacremoses.
  warnings.warn("Recommended: pip install sacremoses.")


['▁Tom', '▁and', '▁Je', 'r', '-', 'b', 'ear']

In [2]:
import pandas as pd


df = pd.read_csv('sentences-translated.csv')


In [3]:
df

Unnamed: 0                              sentence          type  \
0             0                    They are climbing.  subject-verb   
1             1                               I read.  subject-verb   
2             2                             He works.  subject-verb   
3             3                          I will cook.  subject-verb   
4             4                        I am swimming.  subject-verb   
..          ...                                   ...           ...   
120         120           Anna and Elsa share a bond.       complex   
121         121       Tom and Jerry chase each other.       complex   
122         122       Jack and Jill went up the hill.       complex   
123         123  The king and the queen ruled wisely.       complex   
124         124   Mike and his sister study together.       complex   

                                             structure  \
0    [{"subject": "they", "verb": "climb", "verb_te...   
1    [{"subject": "I", "verb": "read", "verb_tense"...   
2    [{"subject": "he", "verb": "work", "verb_tense...   
3    [{"subject": "I", "verb": "cook", "verb_tense"...   
4    [{"subject": "I", "verb": "swim", "verb_tense"...   
..                                                 ...   
120  [{"subject": "Anna", "verb": "share", "verb_te...   
121  [{"subject": "Tom", "verb": "chase", "verb_ten...   
122  [{"subject": "Jack", "verb": "go", "verb_tense...   
123  [{"subject": "king", "verb": "rule", "verb_ten...   
124  [{"subject": "Mike", "verb": "study", "verb_te...   

                                            simple  sim_simple  \
0                               They are climbing.    1.000000   
1                                          I read.    1.000000   
2                                        He works.    1.000000   
3                                     I will cook.    1.000000   
4                                   I am swimming.    1.000000   
..                                             ...         ...   
120        Anna shares a bond. Elsa shares a bond.    0.933623   
121            Tom chases Jerry. Jerry chases Tom.    0.873228   
122  Jack went to the hill. Jill went to the hill.    0.920877   
123               The king ruled. The queen ruled.    0.880852   
124               Mike studies. My sister studies.    0.793314   

                                            comparator  sim_comparator  \
0                                   They are climbing.        1.000000   
1                                              I read.        1.000000   
2                                            He works.        1.000000   
3                                         I will cook.        1.000000   
4                                       I am swimming.        1.000000   
..                                                 ...             ...   
120                  I see an object. I see an object.        0.514783   
121  The [SUBJECT] chases the [OBJECT]. The [SUBJEC...        0.629518   
122                  I went [OBJECT]. I went [OBJECT].        0.551594   
123                                I [VERB]. I [VERB].        0.579115   
124                                I [VERB]. I [VERB].        0.471543   

                                                target  \
0                                   mahuw̃a tsibui-ti.   
1                                        nüü tünia-dü.   
2                                        uhu waakü-dü.   
3                                      nüü [cook]-wei.   
4                                       nüü pahabi-ti.   
..                                                 ...   
120  [bond]-noka [anna]-uu u-[share]-dü. [bond]-nei...   
121  [jerry]-noka [tom]-ii u-naki-dü. [tom]-neika [...   
122  [hill]-neika [jack]-uu ma-[go]-ku. [hill]-neik...   
123         [rule]-ku [king]-ii. [rule]-ku [queen]-uu.   
124      [study]-dü [mike]-ii. [study]-dü [sister]-uu.   

                                           backwards  sim_backwards  
0     

In [4]:
en_sentence = df.iloc[0]['sentence']
pt_sentence = df.iloc[0]['target']
en_sentence,pt_sentence

('They are climbing.', 'mahuw̃a tsibui-ti.')

In [ ]:
en_sentence="You and I  smelled these fish"
pt_sentence="pagwi-neika taa mai-gwana-wei"

In [32]:
pt_sentence="pagwi-neika taa mai-gwana-dü"
en_sentence="You and I smell these flamingo"

In [37]:
en_sentence="The flamingos are eating dinner"
pt_sentence='yotsi-uu tüba-noka u-düka-ti'

In [38]:
# get encoded input vectors

encoder_input_ids = tokenizer(en_sentence, return_tensors="pt", add_special_tokens=False).input_ids.to("cuda")

# create ids of encoded input vectors
with tokenizer.as_target_tokenizer():
    decoder_input_ids = tokenizer(pt_sentence, return_tensors="pt", add_special_tokens=False).input_ids.to("cuda")

outputs = model(input_ids=encoder_input_ids, decoder_input_ids=decoder_input_ids)

encoder_text = tokenizer.convert_ids_to_tokens(encoder_input_ids[0])
decoder_text = tokenizer.convert_ids_to_tokens(decoder_input_ids[0])


/home/remote/miniconda3/envs/kubi/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:3921: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(


In [40]:
from bertviz import head_view
head_view(
    encoder_attention=outputs.encoder_attentions,
    decoder_attention=outputs.decoder_attentions,
    cross_attention=outputs.cross_attentions,
    encoder_tokens= encoder_text,
    decoder_tokens=decoder_text
)

<IPython.core.display.Javascript object>

In [39]:
from bertviz import model_view
model_view(
    encoder_attention=outputs.encoder_attentions,
    decoder_attention=outputs.decoder_attentions,
    cross_attention=outputs.cross_attentions,
    encoder_tokens= encoder_text,
    decoder_tokens=decoder_text
)

<IPython.core.display.Javascript object>

In [ ]:

model_view(
    encoder_attention=outputs.encoder_attentions,
    decoder_attention=outputs.decoder_attentions,
    cross_attention=outputs.cross_attentions,
    encoder_tokens= encoder_text,
    decoder_tokens=decoder_text
)

In [5]:
en_sentence

'They are climbing.'

In [12]:
df

Unnamed: 0                              sentence          type  \
0             0                    They are climbing.  subject-verb   
1             1                               I read.  subject-verb   
2             2                             He works.  subject-verb   
3             3                          I will cook.  subject-verb   
4             4                        I am swimming.  subject-verb   
..          ...                                   ...           ...   
120         120           Anna and Elsa share a bond.       complex   
121         121       Tom and Jerry chase each other.       complex   
122         122       Jack and Jill went up the hill.       complex   
123         123  The king and the queen ruled wisely.       complex   
124         124   Mike and his sister study together.       complex   

                                             structure  \
0    [{"subject": "they", "verb": "climb", "verb_te...   
1    [{"subject": "I", "verb": "read", "verb_tense"...   
2    [{"subject": "he", "verb": "work", "verb_tense...   
3    [{"subject": "I", "verb": "cook", "verb_tense"...   
4    [{"subject": "I", "verb": "swim", "verb_tense"...   
..                                                 ...   
120  [{"subject": "Anna", "verb": "share", "verb_te...   
121  [{"subject": "Tom", "verb": "chase", "verb_ten...   
122  [{"subject": "Jack", "verb": "go", "verb_tense...   
123  [{"subject": "king", "verb": "rule", "verb_ten...   
124  [{"subject": "Mike", "verb": "study", "verb_te...   

                                            simple  sim_simple  \
0                               They are climbing.    1.000000   
1                                          I read.    1.000000   
2                                        He works.    1.000000   
3                                     I will cook.    1.000000   
4                                   I am swimming.    1.000000   
..                                             ...         ...   
120        Anna shares a bond. Elsa shares a bond.    0.933623   
121            Tom chases Jerry. Jerry chases Tom.    0.873228   
122  Jack went to the hill. Jill went to the hill.    0.920877   
123               The king ruled. The queen ruled.    0.880852   
124               Mike studies. My sister studies.    0.793314   

                                            comparator  sim_comparator  \
0                                   They are climbing.        1.000000   
1                                              I read.        1.000000   
2                                            He works.        1.000000   
3                                         I will cook.        1.000000   
4                                       I am swimming.        1.000000   
..                                                 ...             ...   
120                  I see an object. I see an object.        0.514783   
121  The [SUBJECT] chases the [OBJECT]. The [SUBJEC...        0.629518   
122                  I went [OBJECT]. I went [OBJECT].        0.551594   
123                                I [VERB]. I [VERB].        0.579115   
124                                I [VERB]. I [VERB].        0.471543   

                                                target  \
0                                   mahuw̃a tsibui-ti.   
1                                        nüü tünia-dü.   
2                                        uhu waakü-dü.   
3                                      nüü [cook]-wei.   
4                                       nüü pahabi-ti.   
..                                                 ...   
120  [bond]-noka [anna]-uu u-[share]-dü. [bond]-nei...   
121  [jerry]-noka [tom]-ii u-naki-dü. [tom]-neika [...   
122  [hill]-neika [jack]-uu ma-[go]-ku. [hill]-neik...   
123         [rule]-ku [king]-ii. [rule]-ku [queen]-uu.   
124      [study]-dü [mike]-ii. [study]-dü [sister]-uu.   

                                           backwards  sim_backwards  
0     

In [51]:
input_str="Tom and Jer-bear"
with tokenizer.as_target_tokenizer():
    pt_tok = tokenizer.tokenize(input_str)
pt_tok, tokenizer.tokenize(input_str)

/home/remote/miniconda3/envs/kubi/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:3921: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(


(['▁Tom', '▁and', '▁Jer', '-', 'bear'],
 ['▁To', 'm', '▁and', '▁Jer', '-', 'be', 'ar'])

In [55]:
en_tokenizer.tokenize(input_str)

['▁Tom', '▁and', '▁Je', 'r', '-', 'b', 'ear']

In [33]:

input_str = 'Tom and Jerry chase each other.'

inputs = tokenizer(input_str,  return_tensors="pt").to("cuda")

out = model.generate(**inputs, do_sample=True, num_beams=12)#output_attentions=True, output_hidden_states=True, output_scores=True, return_dict_in_generate=True)


In [ ]:
out

In [7]:
out.decoder_hidden_states[0][0].shape

torch.Size([6, 1, 512])

In [8]:
inputs.input_ids.shape, len(input_str)

(torch.Size([1, 17]), 37)

In [369]:
len(tokenizer.encode(decoded_out))

12

In [26]:
out

tensor([[64171,   316,     6,  2972,  2074,    20,   110,    95,   535,   273,
          7110,    25,     0]], device='cuda:0')

In [34]:
decoded_out = tokenizer.decode(out[0], skip_special_tokens=True)
len(decoded_out), decoded_out

(14, 'ta-naki-dü taa')

In [371]:
len(tokenizer.encode(input_str))

11

In [373]:
len(tokenizer.encode(decoded_out))

19

In [73]:
out.sequences[0]

tensor([64171,   316,     6,  2972,  2074,    20,   110,    95,   535,   273,
         7110,    25,     0], device='cuda:0')

In [374]:
out.sequences[0].shape

torch.Size([21])

In [361]:
out.sequences.shape

torch.Size([1, 14])

In [375]:
encoder_attentions  = out.encoder_attentions

In [376]:
decoder_attentions  = out.decoder_attentions

In [377]:
len(decoder_attentions)

21

In [378]:
decoder_attentions[0][0][0].shape

torch.Size([8, 1, 1])

In [379]:
encoder_attentions[0].shape

torch.Size([1, 8, 11, 11])

In [312]:
len(encoder_attentions)

6

In [109]:
torch.sum(attentions[-1][0], dim=1).mean(dim=1)

NameError: name 'attentions' is not defined

In [380]:
input_str, tokenizer.tokenize(input_str)

('The flamingos are eating dinner',
 ['▁The', '▁fl', 'amin', 'gos', '▁are', '▁e', 'a', 'ting', '▁di', 'nner'])

AttributeError: 'tuple' object has no attribute 'shape'

In [381]:
import torch

torch.cat(encoder_attentions, dim=0).sum(dim=0).mean(dim=1)#.argmax(dim=-1)


tensor([[0.1466, 0.3178, 0.5025, 0.9491, 0.3331, 0.4268, 0.2805, 0.4770, 0.4148,
         0.5711, 1.5806],
        [0.2221, 0.2977, 0.5764, 0.8283, 0.4115, 0.2945, 0.2972, 0.4220, 0.2536,
         0.6056, 1.7912],
        [0.4704, 0.4159, 0.5873, 0.5968, 0.4156, 0.2735, 0.4528, 0.4167, 0.4379,
         0.6329, 1.3002],
        [0.3677, 0.4947, 0.5133, 0.5553, 0.4977, 0.5909, 0.6235, 0.4297, 0.3796,
         0.4010, 1.1467],
        [0.3039, 0.5959, 0.5134, 0.4907, 0.3373, 0.5161, 0.2946, 0.2626, 0.4177,
         0.4903, 1.7776],
        [0.3212, 0.4026, 0.4484, 0.5285, 0.3109, 0.3809, 0.3393, 0.3896, 0.5358,
         0.3075, 2.0352],
        [0.1916, 0.5900, 0.5024, 0.5443, 0.3766, 0.5585, 0.5329, 0.3738, 0.5179,
         0.5141, 1.2979],
        [0.2747, 0.3961, 0.5083, 0.5388, 0.2399, 0.3268, 0.2640, 0.4561, 0.4864,
         0.7342, 1.7747]], device='cuda:0')

In [382]:
decoder_attentions[0][0].shape

torch.Size([6, 8, 1, 1])

In [385]:
len(out.cross_attentions)

21

In [387]:
out.cross_attentions[0][0].shape

torch.Size([6, 8, 1, 11])

In [390]:
out.cross_attentions[0][0][0][1]

tensor([[0.0822, 0.0666, 0.0378, 0.0288, 0.0177, 0.0391, 0.0352, 0.0080, 0.0617,
         0.0412, 0.5818]], device='cuda:0')

In [391]:
tokenizer.tokenize(input_str)

['▁The', '▁fl', 'amin', 'gos', '▁are', '▁e', 'a', 'ting', '▁di', 'nner']

In [389]:
out.cross_attentions[0][0][0][0]

tensor([[1.8802e-02, 1.2261e-02, 9.2171e-03, 1.2410e-02, 4.4713e-03, 1.2652e-02,
         8.4564e-03, 6.3204e-04, 3.6829e-03, 7.1876e-03, 9.1023e-01]],
       device='cuda:0')

In [384]:
torch.cat(out.cross_attentions[0], dim=0).shape

torch.Size([36, 8, 1, 11])

In [358]:
len(out.scores)

15

In [309]:
out.sequences.shape


torch.Size([1, 14])

In [205]:
tokenizer.get_src_vocab()['y']

77

In [200]:
vocab_temp  = tokenizer.get_src_vocab()

In [218]:
rev_vocab = {}

for k, v in vocab_temp.items():
    rev_vocab[v] = k

In [393]:
input_str, tokenizer.tokenize(input_str)

('The flamingos are eating dinner',
 ['▁The', '▁fl', 'amin', 'gos', '▁are', '▁e', 'a', 'ting', '▁di', 'nner'])

In [394]:
input_str, tokenizer.tokenize(input_str), decoded_out

('The flamingos are eating dinner',
 ['▁The', '▁fl', 'amin', 'gos', '▁are', '▁e', 'a', 'ting', '▁di', 'nner'],
 'yotsi-uu tüba-noka u-düka-ti')

In [395]:
len(out.scores)

21

In [227]:
o_max

array([   0,    0,    0,   46, 2074,   20])

In [396]:
torch.cat(encoder_attentions, axis=0).sum(dim=0).mean(dim=0)

tensor([[1.0571, 0.6955, 0.4950, 0.7532, 0.2969, 0.1343, 0.1835, 0.1413, 0.1417,
         0.2382, 1.8632],
        [0.2782, 1.2802, 1.3959, 0.6640, 0.0961, 0.0926, 0.0876, 0.0835, 0.1384,
         0.1856, 1.6978],
        [0.2664, 1.3216, 1.2337, 1.1951, 0.1981, 0.1149, 0.1071, 0.0911, 0.1325,
         0.1628, 1.1767],
        [0.2793, 0.3896, 1.1001, 1.6852, 0.5433, 0.1630, 0.1599, 0.1593, 0.1255,
         0.2028, 1.1918],
        [0.4540, 0.1064, 0.2789, 0.6639, 1.3444, 0.4953, 0.2524, 0.4662, 0.1890,
         0.4130, 1.3364],
        [0.0863, 0.1169, 0.1733, 0.4425, 0.3773, 0.9402, 1.1362, 0.5941, 0.3583,
         0.4330, 1.3418],
        [0.1019, 0.1755, 0.1921, 0.3910, 0.2643, 1.2746, 0.7230, 1.0437, 0.4353,
         0.5044, 0.8941],
        [0.1862, 0.1487, 0.2200, 0.2392, 0.3345, 0.6330, 0.6769, 1.1302, 0.5886,
         0.6804, 1.1623],
        [0.0826, 0.1537, 0.1527, 0.1949, 0.1051, 0.3292, 0.4137, 0.2689, 1.2857,
         1.4489, 1.5647],
        [0.1270, 0.1564, 0.1702, 0.39

In [332]:
out.sequences_scores

tensor([-0.0158], device='cuda:0')

In [329]:
encoder_attentions[0][0].shape

torch.Size([1, 8, 10, 10])

In [328]:
out.cross_attentions[0][0].shape

torch.Size([6, 8, 1, 10])

In [349]:
len(out.scores[0])

6

In [357]:
out.sequences.shape

torch.Size([1, 14])

In [356]:
out.items()

odict_items([('sequences', tensor([[64171,   439,    28,   147,    20,    46,    46,   316,     6,  2972,
          2074,    20,   110,     0]], device='cuda:0')), ('sequences_scores', tensor([-0.0158], device='cuda:0')), ('scores', (tensor([[ -5.8960, -17.5750, -10.3938,  ..., -17.5226, -17.5245,     -inf],
        [ -5.8960, -17.5750, -10.3938,  ..., -17.5226, -17.5245,     -inf],
        [ -5.8960, -17.5750, -10.3938,  ..., -17.5226, -17.5245,     -inf],
        [ -5.8960, -17.5750, -10.3938,  ..., -17.5226, -17.5245,     -inf],
        [ -5.8960, -17.5750, -10.3938,  ..., -17.5226, -17.5245,     -inf],
        [ -5.8960, -17.5750, -10.3938,  ..., -17.5226, -17.5245,     -inf]],
       device='cuda:0'), tensor([[-19.3948, -28.9771, -21.7005,  ..., -28.9463, -28.9501,     -inf],
        [-18.4509, -27.0139, -19.8635,  ..., -26.9801, -26.9817,     -inf],
        [-20.3799, -29.4480, -23.0312,  ..., -29.4090, -29.4112,     -inf],
        [-25.9273, -34.0377, -26.9265,  ..., -34.0519, -

In [397]:
for score in out.scores:
    o_max = score.argmax(dim=1).detach().cpu().numpy()
    merged_=""
    for item in o_max[:]:
        merged_+=rev_vocab[item]
        merged_+= " "
    print(merged_)
    print(score.argmax(dim=1))
    print(score.max(dim=1).values)

    # print(o_max[0])

▁yo ▁yo ▁yo ▁yo ▁yo ▁yo 
tensor([439, 439, 439, 439, 439, 439], device='cuda:0')
tensor([-0.1905, -0.1905, -0.1905, -0.1905, -0.1905, -0.1905], device='cuda:0')
t ah ü ' a kit 
tensor([  28, 1079, 1060,   15,   25, 6512], device='cuda:0')
tensor([-2.8252e-05, -2.4119e-03, -7.7486e-06, -2.3842e-07,  0.0000e+00,
         0.0000e+00], device='cuda:0')
si abi ba ada - a 
tensor([  147, 10439,   158,  1685,    20,    25], device='cuda:0')
tensor([ 0.0000e+00, -1.1921e-07, -1.9854e-02, -3.0369e-01, -1.3851e-04,
         0.0000e+00], device='cuda:0')
- - - u - - 
tensor([20, 20, 20, 46, 20, 20], device='cuda:0')
tensor([ 0.0000,  0.0000,  0.0000, -0.0007,  0.0000,  0.0000], device='cuda:0')
u u u u u u 
tensor([46, 46, 46, 46, 46, 46], device='cuda:0')
tensor([-1.3471e-05, -4.5299e-06, -1.5020e-05,  0.0000e+00, -2.2650e-06,
         0.0000e+00], device='cuda:0')
u u u ▁t u u 
tensor([ 46,  46,  46, 316,  46,  46], device='cuda:0')
tensor([ 0.0000,  0.0000,  0.0000, -0.0077,  0.0000,  0.0000],

In [335]:
decoded_out

'yotsi-uu tsibui-ti'

In [263]:
x=out.scores[0]

In [251]:
x.shape

torch.Size([6, 64172])

In [264]:
x[torch.isinf(x)]=-1

In [267]:
x.argmax(dim=0)

tensor([0, 0, 0,  ..., 0, 0, 0], device='cuda:0')

In [237]:
out.scores[-2].argmax(dim=1)

tensor([   0,    0, 1060,    0,  110,    0], device='cuda:0')

In [216]:
torch.cat(out.scores, dim=0).shape

torch.Size([132, 64172])

In [140]:
len(out.cross_attentions[0][0])

6

In [124]:
df.iloc[0]

sentence                                         They are climbing.
type                                                   subject-verb
structure         [{"subject": "they", "verb": "climb", "verb_te...
simple                                           They are climbing.
sim_simple                                                      1.0
comparator                                       They are climbing.
sim_comparator                                                  1.0
target                                           mahuw̃a tsibui-ti.
backwards                                        They are climbing.
sim_backwards                                                   1.0
tense                                                           VBG
Name: 0, dtype: object

In [114]:
torch.cat(encoder_attentions, dim=0).sum( dim=(0, 1)).argmax(dim=-1)


tensor([7, 7, 7, 7, 5, 7, 7, 7], device='cuda:0')

In [165]:
out.

'Mikei-neika Mikei-dü ma-yadohi-dü'

In [183]:
attentions[0].shape

torch.Size([1, 8, 15, 15])

In [188]:
torch.cat(attentions, dim=0).sum(dim=0).mean(dim=1).argmax(dim=-1).shape

torch.Size([8])

In [125]:
def analyze_attention(attentions):
    # Sum the attention weights across all layers and heads
    attention_tensor = torch.cat(attentions, dim=0)
    summed_attention = torch.sum(attention_tensor, dim=0)
    # Average the summed attention across all layers and heads
    averaged_attention = torch.mean(summed_attention, dim=1)
    return averaged_attention

In [90]:
def find_alignment(attention_matrix):
    # For each target word, find the source word with the highest attention weight
    alignment = attention_matrix.argmax(dim=-1)
    return alignment


In [141]:
decoded_out.split()

['kamü-uu', "kwatsa'i-ku"]

In [130]:
len(input_str)

31

In [129]:
attention_matrix.shape

torch.Size([8, 12])

In [204]:
out.sequences

tensor([[64171, 27749,    33,    20,   133,  4471, 27749,    33,    20,    44,
          1060,    95,    20,    77,  3890,   257,    20,    44,  1060,     0]],
       device='cuda:0')

In [126]:
attention_matrix = analyze_attention(attentions)
alignment = find_alignment(attention_matrix)


In [137]:
alignment

tensor([11, 11, 11, 11, 11, 11, 11, 11], device='cuda:0')

In [78]:
import torch
conf = []

for s in out.scores:
    max_probs = torch.softmax(s, dim=-1).max(dim=-1).values

    conf.append(max_probs)

In [74]:
tokenizer.encode(decoded_out)

[17634, 60, 20, 4261, 557, 5934, 33, 14243, 20, 192, 0]

In [79]:
conf

[tensor([0.7321, 0.7321, 0.7321, 0.7321, 0.7321, 0.7321], device='cuda:0'),
 tensor([0.9882, 1.0000, 1.0000, 1.0000, 0.9979, 1.0000], device='cuda:0'),
 tensor([0.9982, 0.9764, 1.0000, 1.0000, 1.0000, 1.0000], device='cuda:0'),
 tensor([1.0000, 1.0000, 0.9956, 0.9999, 0.9982, 1.0000], device='cuda:0'),
 tensor([1.0000, 1.0000, 0.9422, 1.0000, 0.8558, 0.8406], device='cuda:0'),
 tensor([1.0000, 1.0000, 1.0000, 0.9997, 0.9267, 0.7960], device='cuda:0'),
 tensor([1.0000, 0.9573, 1.0000, 1.0000, 1.0000, 1.0000], device='cuda:0'),
 tensor([1.0000, 1.0000, 0.9973, 1.0000, 1.0000, 0.8440], device='cuda:0'),
 tensor([0.5035, 0.9490, 0.9992, 1.0000, 1.0000, 1.0000], device='cuda:0'),
 tensor([1.0000, 0.7331, 0.7569, 1.0000, 1.0000, 1.0000], device='cuda:0'),
 tensor([0.6511, 0.7864, 1.0000, 1.0000, 1.0000, 1.0000], device='cuda:0'),
 tensor([1.0000, 0.9999, 1.0000, 1.0000, 1.0000, 0.9999], device='cuda:0'),
 tensor([1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 0.7869], device='cuda:0'),
 tensor([1.0

In [75]:
conf

[tensor([0.8635, 0.8635, 0.8635, 0.8635, 0.8635, 0.8635], device='cuda:0'),
 tensor([0.7854, 0.6606, 0.9995, 0.9987, 0.8528, 0.7037], device='cuda:0'),
 tensor([1.0000, 1.0000, 1.0000, 1.0000, 0.9999, 0.9996], device='cuda:0'),
 tensor([1.0000, 1.0000, 1.0000, 0.9990, 0.9992, 0.9956], device='cuda:0'),
 tensor([0.6444, 1.0000, 0.9761, 0.4662, 0.9760, 0.9727], device='cuda:0'),
 tensor([0.6636, 1.0000, 0.9992, 1.0000, 0.7966, 0.9177], device='cuda:0'),
 tensor([1.0000, 0.8006, 0.5990, 1.0000, 0.9874, 1.0000], device='cuda:0'),
 tensor([0.8143, 1.0000, 0.9993, 1.0000, 0.4484, 1.0000], device='cuda:0'),
 tensor([1.0000, 0.7809, 1.0000, 0.7692, 1.0000, 0.9994], device='cuda:0'),
 tensor([1.0000, 1.0000, 1.0000, 1.0000, 0.9880, 1.0000], device='cuda:0'),
 tensor([1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000], device='cuda:0'),
 tensor([1.0000, 1.0000, 0.8233, 1.0000, 1.0000, 1.0000], device='cuda:0'),
 tensor([1.0000, 0.9992, 1.0000, 1.0000, 1.0000, 0.7313], device='cuda:0'),
 tensor([1.0

In [25]:
embeddings = []
for input_text in pt_words:
    inputs = tokenizer(input_text,  return_tensors="pt").to("cuda")

    out = model.get_encoder()(**inputs)
    out = out.last_hidden_state.mean(dim=1).detach().flatten().cpu().numpy()
    embeddings.append(out)

In [10]:
import numpy as np
np.array(embeddings).shape

(100, 512)

In [53]:
unique_tense = np.unique(tense)

In [55]:
tense_to_int = {}

for idx in range(len(unique_tense)):
    tense_to_int[unique_tense[idx]] = idx

In [26]:
tense_encoded = []

for item in tense:
    if item in tense_to_past_present:
        tense_encoded.append(tense_to_past_present[item])
    else:
        tense_encoded.append(-1)
tense_encoded

[1,
 1,
 1,
 1,
 -1,
 1,
 1,
 1,
 0,
 1,
 1,
 -1,
 -1,
 -1,
 0,
 -1,
 -1,
 1,
 -1,
 -1,
 1,
 1,
 0,
 1,
 -1,
 1,
 1,
 1,
 1,
 1,
 -1,
 1,
 -1,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 1,
 -1,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 -1,
 -1,
 1,
 0,
 -1,
 1,
 1,
 1,
 1,
 -1,
 0,
 0,
 1,
 1,
 1,
 -1,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 -1,
 0,
 1,
 1,
 0,
 0,
 1,
 1,
 -1,
 0,
 0,
 -1,
 0,
 1,
 0,
 1,
 1,
 -1,
 -1,
 1,
 0,
 0,
 0,
 1,
 0,
 1,
 -1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 -1,
 -1,
 1,
 -1,
 0,
 1,
 0,
 1,
 1,
 -1,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 -1,
 0,
 0,
 0,
 1,
 -1,
 0,
 1,
 -1,
 0,
 1,
 1,
 -1,
 1,
 1,
 -1,
 -1,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 1,
 -1,
 0,
 1,
 0,
 0,
 1,
 1,
 -1,
 1,
 1,
 -1,
 1,
 -1,
 1,
 1,
 1,
 -1,
 0,
 1,
 1,
 -1,
 -1,
 -1,
 0,
 0,
 -1,
 1,
 0,
 1,
 -1,
 -1,
 0,
 1,
 1,
 0,
 -1,
 -1,
 0,
 1,
 1,
 1,
 -1,
 0,
 1,
 -1,
 0,
 1,
 -1,
 1,
 1,
 -1,
 0,
 0,
 1,
 1,
 1,
 1,
 -1,
 -1,
 1,
 0,
 1,
 1,
 1,
 -1,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 1,

In [27]:
embeddings = np.array(embeddings)
tense_encoded=np.array(tense_encoded)

tense_not_future = np.argwhere(tense_encoded > -1).flatten()

tense_encoded_=tense_encoded[tense_not_future]
embeddings_ = embeddings[tense_not_future]

In [28]:
x_test_index = np.arange(tense_encoded_.shape[0])
y_test_index = np.arange(tense_encoded_.shape[0])

In [14]:
from sklearn.ensemble import RandomForestRegressor

from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, mean_absolute_error

In [29]:
# X_train, X_test, y_train, y_test = train_test_split(embeddings, tense_encoded, test_size=0.2, random_state=42)
x_train_idx, x_test_idx, y_train_idx, y_test_idx = train_test_split(x_test_index, y_test_index, test_size=0.2, random_state=42)


X_train = embeddings_[x_train_idx]
y_train =  tense_encoded_[x_train_idx]

X_test = embeddings_[x_test_idx]
y_test =  tense_encoded_[y_test_idx]


# rfr = RandomForestRegressor(n_estimators=100)
# rfr.fit(X_train, y_train)
# preds = rfr.predict(X_test)


# mse = mean_squared_error(y_test, preds)
# mae = mean_absolute_error(y_test, preds)

# print(f"text-embedding-3-small performance on 1k Amazon reviews: mse={mse:.2f}, mae={mae:.2f}")

In [16]:
rfr.score(X_test, y_test)

0.6714883116883117

In [62]:
en_words

[2, 2, 3, 5, 1, 4, 1, 1, 1, 1, 2, 2, 5, 5, 5, 2, 0, 2, 1, 1]

In [30]:
from sklearn.linear_model import LogisticRegression


clf = LogisticRegression()
clf.fit(X_train, y_train)
score = clf.score(X_test, y_test)
print(score)
preds = clf.predict_proba(X_test)

0.9801488833746899


In [33]:
X_test.shape

(806, 512)

In [87]:
preds[0]

array([0.34931448, 0.65068552])

In [93]:
tense[7:9]

['VB', 'VBG']

In [94]:
en_words[7:9]

['You will sneeze.', 'This coyote is going to write these rocks.']

In [89]:
np.not_equal(y_test, preds.argmax(axis=1))

array([False, False, False, False, False, False, False,  True,  True,
        True, False, False, False, False, False, False, False, False,
       False,  True])

In [64]:
y_test

[1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0]

[1,
 1,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 1]

In [47]:
bmse = mean_squared_error(y_test, np.repeat(np.mean(y_test), len(y_test)))
bmae = mean_absolute_error(y_test, np.repeat(np.mean(y_test), len(y_test)))
print(
    f"Dummy mean prediction performance on Amazon reviews: mse={bmse:.2f}, mae={bmae:.2f}"
)

Dummy mean prediction performance on Amazon reviews: mse=0.24, mae=0.48


In [35]:
last_hidden_state = outputs.last_hidden_state
# Mean pooling
pooled_output = last_hidden_state.mean(dim=1)


AttributeError: 'Tensor' object has no attribute 'last_hidden_state'